In [1]:
pip install clickhouse-driver

Note: you may need to restart the kernel to use updated packages.


In [54]:
from kafka import KafkaConsumer
from kafka import KafkaProducer
from elasticsearch import Elasticsearch
import time
import re
import json
from json import loads
from time import sleep
from json import dumps
import requests
import datetime
import pandas as pd

In [262]:
from clickhouse_driver import Client
client = Client(host='localhost', password='1994', settings={'use_numpy': True, 'strings_encoding ':'Unicode'})

In [5]:
client.execute('CREATE DATABASE IF NOT EXISTS chdb')

[]

In [261]:
client.execute('SHOW DATABASES')

[array(['chdb'], dtype=object),
 array(['default'], dtype=object),
 array(['system'], dtype=object)]

In [251]:
client.execute('drop table chdb.table')

[]

In [252]:
client.execute('\
    CREATE TABLE IF NOT EXISTS chdb.table(\
    id UInt64,\
    year UInt16,\
    month UInt16,\
    day UInt16,\
    hour UInt16,\
    minute UInt16,\
    senderName String,\
    senderUsername String,\
    hashtags String,\
    keywords String\
) ENGINE = MergeTree()\
   PARTITION BY (year,month,day)\
    ORDER BY  (id,year,month,day,hour,minute)\
     PRIMARY KEY (id);')

[]

In [98]:
df=pd.DataFrame(columns=['id','year', 'month','day','hour','minute','senderName','senderUsername','hashtags', 'links', 'keywords'])
df

Empty DataFrame
Columns: [id, year, month, day, hour, minute, senderName, senderUsername, hashtags, links, keywords]
Index: []

In [19]:
df

id  year month day hour minute      senderName   senderUsername  \
0  327731471  1400     4  28    0     10        لولو خان         looolooo   
1  327731458  1400     4  28    0     10  وقایع اقتصادیه  3_white_soldier   
2  327731422  1400     4  28    0      9       پیشگو2021        pish_2021   
3  327731402  1400     4  28    0      9       ملیکا حجت      melikahujat   
4  327731372  1400     4  28    0      9       Nikjouyan        nikjouyan   
5  327731368  1400     4  28    0      9        امیر سام        amirsaam2   
6  327731363  1400     4  28    0      9       سعید اشتر             sady   
7  327731334  1400     4  28    0      9  همفکری بورسی 2           zian55   
8  327731323  1400     4  28    0      8     سیگنال دقیق            isuzu   
9  327731294  1400     4  28    0      8             Ali      teymoor9075   

  hashtags links                                           keywords  
0    خاور,        شرکت,سود,اصلاح,سهام,بسته,بعدش,بهتون,بکار,بیسوا...  
1   شبندر,                                              سود,پرداخت,  
2      دی,                                               فردا,نماد,  
3   وگردش,                رسما,خرد,خبری,حق,تقدم‌ها,ای,افزایش,کشیدن,  
4    غنوش,        تشکر,تدریجی,بهترین‌ها,بنده,بنا,بعنوان,بحساب,با...  
5    غاذر,                           صف,فردا,فروش,مطمئن,نوسانه,پله,  
6                 ازش,الان,امثال,اونی,بزرگتر,بغلش,بورست,تاریخ,تر...  
7      دی,                                            دی,خرید,فروش,  
8                             انتهای,صف,رد,درو,خودت,بعدش,بازار,۷۸۰,  
9      دی,                               خریدار,عکس,فروشنده,نگاه,ک,

In [254]:
consumer = KafkaConsumer(
    'persistence',
     bootstrap_servers=['192.168.1.3:9092'],
     auto_offset_reset='earliest',
     enable_auto_commit=True,
     group_id='my-group3',
     api_version=(0,10),
     value_deserializer=lambda x: loads(x.decode('utf-8')))

for message in consumer:
    message = message.value
    print(message)
    
    if 'content' not in message:
        continue    
    
    id=int(message['id'])
    content=message['content']
    date = datetime.datetime.strptime(message['sendTimePersian'], "%Y/%m/%d  %H:%M")
    year=date.year
    month=date.month
    day=date.day
    hour=date.hour
    minute=date.minute
    
    new_row={'id':id,'year':year,'month':month,'day':day,'hour':hour,'minute':minute,'senderName':message['senderName'],
             'senderUsername':message['senderUsername'],'hashtags':message['hashtags'], 'links':message['links'], 'keywords':message['keywords']}
    df=df.append(new_row, ignore_index=True)

{'id': '327966429', 'sendTime': '2021-07-19T11:04:47Z', 'sendTimePersian': '1400/04/28 15:34', 'senderName': 'shima_shahmoradi', 'senderUsername': 'shimashahmoradi', 'senderProfileImage': '432eafca-96ce-4f40-a55c-a4bc709f357c', 'content': '#شاخص_بورس قراره اصلاح سنگین بکنه\nاما میکشوندش تا دولت بعد...\nنمیخوان این سقوط به اسم خودشون تموم شه', 'type': 'twit', 'scoredPostDate': '1626692687683', 'finalPullDatePersian': '', 'hashtags': ['شاخص_بورس'], 'links': [], 'keywords': ['شه', 'قراره', 'نمیخوان', '…', 'دولت']}
{'id': '327966397', 'sendTime': '2021-07-19T11:04:33Z', 'sendTimePersian': '1400/04/28 15:34', 'senderName': 'یاسر', 'senderUsername': 'yaser24434', 'senderProfileImage': 'default', 'content': '#کیسون', 'type': 'twit', 'imageUid': '1638ccea-171e-4424-91f1-ab2b43b2b0bc', 'mediaContentType': 'image/jpeg', 'scoredPostDate': '1626692722741', 'finalPullDatePersian': '', 'hashtags': ['کیسون'], 'links': [], 'keywords': ['کیسون']}
{'id': '327966657', 'sendTime': '2021-07-19T11:06:35Z', 

KeyboardInterrupt: 

In [61]:
df

id  year month day hour minute     senderName   senderUsername  \
0     327959859  1400     4  28   14     43          برزگر         iranman2   
1     327959830  1400     4  28   14     42            H-A  mfdonline204802   
2     327959717  1400     4  28   14     41         mo2858           mo2858   
3     327959712  1400     4  28   14     41          Prime        prime1356   
4     327959709  1400     4  28   14     41     قزوین بورس           sagard   
...         ...   ...   ...  ..  ...    ...            ...              ...   
2107  327964821  1400     4  28   15     19      سرداربیسر       sar1350dar   
2108  327964811  1400     4  28   15     19        سهامدار          fun9990   
2109  327964754  1400     4  28   15     18          namet           namet5   
2110  327964959  1400     4  28   15     20        sohil64          sohil64   
2111  327964940  1400     4  28   15     20  Helena.Hanafi         h_hanafi   

          hashtags links                                           keywords  
0      [شاخص_بورس]    []  [تعطیله, تعطیل, تصمیمی, ایران, اونها, اعتراضات...  
1               []    []  [امروز, اینها, راسخ, بلند, تاثیری, جو, خال, خو...  
2           [فروی]    []  [حجم, جایزه, بتونه, اینهمه, امروز, اعمال, پایانی]  
3               []    []         [شر, صف, میلیونی, نقطه, هفته, پارسال, ۱۰۰]  
4           [کاما]    []                                               [❤️]  
...            ...   ...                                                ...  
2107       [قشرین]    []  [درموقعیتی, درجیب, حقوقی, باشدبایدحقوقی, اگرچن...  
2108  [شپنا, شستا]    []  [شپنا, شبیه, سود, ستاره, خلیج, حاشیه‌ای, توسط,...  
2109        [برکت]    []  [تهران-, بهادار, بازار, ایرنا-, ایران, اوراق, ...  
2110            []    []  [نا, ناهمواری, وضعیت, ونوسان, وپایین, چروند, گ...  
2111       [غسالم]    []  [), :, ؟!, آب, آخه, آینده, ادم, الخالق, خوردن,...  

[2112 rows x 11 columns]

In [255]:
df=df.drop_duplicates(subset='id' ,keep='first').reset_index(drop=True)
df

id  year month day hour minute    senderName senderUsername  \
0    327964902  1400     4  28   15     19        MINEGZ         mine92   
1    327964883  1400     4  28   15     19  موج سوار (2)  reza1365rezaa   
2    327964826  1400     4  28   15     19         اهورا       msm47047   
3    327964821  1400     4  28   15     19     سرداربیسر     sar1350dar   
4    327964811  1400     4  28   15     19       سهامدار        fun9990   
..         ...   ...   ...  ..  ...    ...           ...            ...   
388  328571296  1400     4  29   19     18    مهدی ایمنی     mahdiimeni   
389  328571208  1400     4  29   19     18          وحید        vma1363   
390  328571428  1400     4  29   19     18          حامد     hamedhemat   
391  328571626  1400     4  29   19     19     سهام همزن     mahaaan220   
392  328571569  1400     4  29   19     19        وتجارت     va_tejarat   

         hashtags links                                           keywords  
0          [غشان]    []  [غشان, خبری, تومن, بعد🤫🤫🤫, بترکونه💣💣💣, اون, ؟,...  
1     [شاخص_بورس]    []                       [رکورد, نامردا, نظرم, چندتا]  
2         [وسپهر]    []  [حرو, تورو, بازیگر, اونایین, اقوامش, ارادت, …ا...  
3         [قشرین]    []  [درموقعیتی, درجیب, حقوقی, باشدبایدحقوقی, اگرچن...  
4    [شپنا, شستا]    []  [شپنا, شبیه, سود, ستاره, خلیج, حاشیه‌ای, توسط,...  
..            ...   ...                                                ...  
388       [وبشهر]    []                                            [وبشهر]  
389       [بوعلی]    []                                            [بوعلی]  
390       [ثعمرا]    []  [خرد, تکنیکالی, تعطیل, تاپ, بنیاد, بازار, انشا...  
391            []    []  [بحث, بطور, تحصیل, تصور, تقریبا, ثروتمندی, جغر...  
392            []    []                                              [👌👌👌]  

[393 rows x 11 columns]

In [155]:
df

id  year month day hour minute             senderName  \
0    327964902  1400     4  28   15     19                 MINEGZ   
1    327964883  1400     4  28   15     19           موج سوار (2)   
2    327964826  1400     4  28   15     19                  اهورا   
3    327964821  1400     4  28   15     19              سرداربیسر   
4    327964811  1400     4  28   15     19                سهامدار   
..         ...   ...   ...  ..  ...    ...                    ...   
96   327967003  1400     4  28   15     40  دلخوشی های صد کلمه ای   
97   327967082  1400     4  28   15     41                      N   
98   327967059  1400     4  28   15     41                  sadra   
99   327967046  1400     4  28   15     40              علی کریمی   
100  327967041  1400     4  28   15     40                   bsam   

    senderUsername      hashtags links  \
0           mine92        [غشان]    []   
1    reza1365rezaa   [شاخص_بورس]    []   
2         msm47047       [وسپهر]    []   
3       sar1350dar       [قشرین]    []   
4          fun9990  [شپنا, شستا]    []   
..             ...           ...   ...   
96       rezagisrs        [خاور]    []   
97        nstn2222            []    []   
98     ela13600000            []    []   
99         seraj61       [سبزوا]    []   
100           bsam            []    []   

                                              keywords  
0    [غشان, خبری, تومن, بعد🤫🤫🤫, بترکونه💣💣💣, اون, ؟,...  
1                         [رکورد, نامردا, نظرم, چندتا]  
2    [حرو, تورو, بازیگر, اونایین, اقوامش, ارادت, …ا...  
3    [درموقعیتی, درجیب, حقوقی, باشدبایدحقوقی, اگرچن...  
4    [شپنا, شبیه, سود, ستاره, خلیج, حاشیه‌ای, توسط,...  
..                                                 ...  
96                                  [دوستان, مرداد, ۵]  
97                                     [درایام, مجامع]  
98                                   [شاه, ماهی, پیام]  
99          [فراهانی, منعکس, نامه, نگاری, همون, چجوری]  
100                                         [دمت, گرم]  

[101 rows x 11 columns]

In [256]:
df2=pd.DataFrame(columns=['id','year', 'month', 'day', 'hour', 'minute','senderName','senderUsername','hashtags', 'keywords'])
df2

Empty DataFrame
Columns: [id, year, month, day, hour, minute, senderName, senderUsername, hashtags, keywords]
Index: []

In [257]:
for i in range(len(df)):
    if df.iloc[i,8]==[]:
        listToStr = ' '.join([str(elem) for elem in df.iloc[i,10]])
        
        new_row={'id':df.iloc[i,0],'year':df.iloc[i,1], 'month':df.iloc[i,2], 'day':df.iloc[i,3], 'hour':df.iloc[i,4],
        'minute':df.iloc[i,5],'senderName':df.iloc[i,6],'senderUsername':df.iloc[i,7],'hashtags':'', 'keywords':listToStr}
        df2=df2.append(new_row, ignore_index=True) 
        
    else:
        for j in df.iloc[i,8]:
            listToStr = ' '.join([str(elem) for elem in df.iloc[i,10]])
            
            new_row={'id':df.iloc[i,0],'year':df.iloc[i,1], 'month':df.iloc[i,2], 'day':df.iloc[i,3], 'hour':df.iloc[i,4],
            'minute':df.iloc[i,5],'senderName':df.iloc[i,6],'senderUsername':df.iloc[i,7],'hashtags':j, 'keywords':listToStr}
            df2=df2.append(new_row, ignore_index=True) 


In [258]:
df2

id  year month day hour minute    senderName senderUsername  \
0    327964902  1400     4  28   15     19        MINEGZ         mine92   
1    327964883  1400     4  28   15     19  موج سوار (2)  reza1365rezaa   
2    327964826  1400     4  28   15     19         اهورا       msm47047   
3    327964821  1400     4  28   15     19     سرداربیسر     sar1350dar   
4    327964811  1400     4  28   15     19       سهامدار        fun9990   
..         ...   ...   ...  ..  ...    ...           ...            ...   
407  328571296  1400     4  29   19     18    مهدی ایمنی     mahdiimeni   
408  328571208  1400     4  29   19     18          وحید        vma1363   
409  328571428  1400     4  29   19     18          حامد     hamedhemat   
410  328571626  1400     4  29   19     19     سهام همزن     mahaaan220   
411  328571569  1400     4  29   19     19        وتجارت     va_tejarat   

      hashtags                                           keywords  
0         غشان          غشان خبری تومن بعد🤫🤫🤫 بترکونه💣💣💣 اون ؟ 🤔🤔  
1    شاخص_بورس                            رکورد نامردا نظرم چندتا  
2        وسپهر       حرو تورو بازیگر اونایین اقوامش ارادت …اده‌تر  
3        قشرین  درموقعیتی درجیب حقوقی باشدبایدحقوقی اگرچندروز ...  
4         شپنا  شپنا شبیه سود ستاره خلیج حاشیه‌ای توسط تلقین ا...  
..         ...                                                ...  
407      وبشهر                                              وبشهر  
408      بوعلی                                              بوعلی  
409      ثعمرا  خرد تکنیکالی تعطیل تاپ بنیاد بازار انشالاه انت...  
410             بحث بطور تحصیل تصور تقریبا ثروتمندی جغرافیایی ...  
411                                                           👌👌👌  

[412 rows x 10 columns]

In [111]:
for i in range(len(df)):
    client.execute(
    f"INSERT INTO chdb.table VALUES ({df.iloc[i,0]},{df.iloc[i,1]},{df.iloc[i,2]},{df.iloc[i,3]},{df.iloc[i,4]},{df.iloc[i,5]},'{df.iloc[i,6]}','{df.iloc[i,7]}',{df.iloc[i,8]},{df.iloc[i,9]},{df.iloc[i,10]})")

ServerException: Code: 62.
DB::Exception: Cannot parse expression of type Array(String) here: [b'\xd8\xba\xd8\xb4\xd8\xa7\xd9\x86'],[],[b'\xd8\xba\xd8\xb4\xd8\xa7\xd9\x86', b'\xd8\xae\xd8\xa8\xd8\xb1\xdb\x8c', b'\xd8\xaa\xd9\x88\xd9\x85\xd9\x86', b'\xd8\. Stack trace:

0. DB::Exception::Exception(std::__1::basic_string<char, std::__1::char_traits<char>, std::__1::allocator<char> > const&, int, bool) @ 0x8d31b5a in /usr/bin/clickhouse
1. DB::ValuesBlockInputFormat::parseExpression(DB::IColumn&, unsigned long) @ 0x1084250a in /usr/bin/clickhouse
2. DB::ValuesBlockInputFormat::readRow(std::__1::vector<COW<DB::IColumn>::mutable_ptr<DB::IColumn>, std::__1::allocator<COW<DB::IColumn>::mutable_ptr<DB::IColumn> > >&, unsigned long) @ 0x1083f65b in /usr/bin/clickhouse
3. DB::ValuesBlockInputFormat::generate() @ 0x1083e99c in /usr/bin/clickhouse
4. DB::ISource::tryGenerate() @ 0x106dfe35 in /usr/bin/clickhouse
5. DB::ISource::work() @ 0x106dfa1a in /usr/bin/clickhouse
6. DB::InputStreamFromInput

In [259]:
client.insert_dataframe('INSERT INTO chdb.table VALUES', df2)

Error on localhost:9000 ping: [WinError 10053] An established connection was aborted by the software in your host machine
Connection was closed, reconnecting.


412

In [263]:
client.execute('SELECT * FROM chdb.table')

[array([327745361, 1400, 4, 28, 6, 29, 'امیدرضا110', 'omidreza1360', 'غگل',
        'صعود پشیمون'], dtype=object),
 array([327800936, 1400, 4, 28, 9, 34, 'شفا  خانه بورس ', 'rakanafi',
        'بورس', 'نفس بورس'], dtype=object),
 array([327955176, 1400, 4, 28, 14, 8, 'Morteza', 'morteza_ths', 'شپلی',
        'اصن اعلام الان الانم انداختن برنده بچه تحویل تنظیم جالبه حاضر آدم حتما حضور خواهم_گفت خودشون دقیق ر رسیده ریزش ریش زدن زمان زمانی ۶۰۰'],
       dtype=object),
 array([327964754, 1400, 4, 28, 15, 18, 'namet', 'namet5', 'برکت',
        'تهران- بهادار بازار ایرنا- ایران اوراق اعلام آتی ؛ . یکشنبه بورس'],
       dtype=object),
 array([327964811, 1400, 4, 28, 15, 19, 'سهامدار', 'fun9990', 'شپنا',
        'شپنا شبیه سود ستاره خلیج حاشیه\u200cای توسط تلقین اولیه گردی'],
       dtype=object),
 array([327964811, 1400, 4, 28, 15, 19, 'سهامدار', 'fun9990', 'شستا',
        'شپنا شبیه سود ستاره خلیج حاشیه\u200cای توسط تلقین اولیه گردی'],
       dtype=object),
 array([327964821, 1400, 4, 28, 15

In [188]:
df2

id             datetime             senderName senderUsername  \
0    327964902  1400-04-28 15:19:00                 MINEGZ         mine92   
1    327964883  1400-04-28 15:19:00           موج سوار (2)  reza1365rezaa   
2    327964826  1400-04-28 15:19:00                  اهورا       msm47047   
3    327964821  1400-04-28 15:19:00              سرداربیسر     sar1350dar   
4    327964811  1400-04-28 15:19:00                سهامدار        fun9990   
..         ...                  ...                    ...            ...   
99   327967003  1400-04-28 15:40:00  دلخوشی های صد کلمه ای      rezagisrs   
100  327967082  1400-04-28 15:41:00                      N       nstn2222   
101  327967059  1400-04-28 15:41:00                  sadra    ela13600000   
102  327967046  1400-04-28 15:40:00              علی کریمی        seraj61   
103  327967041  1400-04-28 15:40:00                   bsam           bsam   

      hashtags links                                           keywords  
0         غشان    []          غشان خبری تومن بعد🤫🤫🤫 بترکونه💣💣💣 اون ؟ 🤔🤔  
1    شاخص_بورس    []                            رکورد نامردا نظرم چندتا  
2        وسپهر    []       حرو تورو بازیگر اونایین اقوامش ارادت …اده‌تر  
3        قشرین    []  درموقعیتی درجیب حقوقی باشدبایدحقوقی اگرچندروز ...  
4         شپنا    []  شپنا شبیه سود ستاره خلیج حاشیه‌ای توسط تلقین ا...  
..         ...   ...                                                ...  
99        خاور    []                                     دوستان مرداد ۵  
100               []                                       درایام مجامع  
101               []                                      شاه ماهی پیام  
102      سبزوا    []                فراهانی منعکس نامه نگاری همون چجوری  
103               []                                            دمت گرم  

[104 rows x 7 columns]